# Compare original shift inversion algorithm to new one

In [ ]:
%matplotlib ipympl
from matplotlib import pyplot as plt

In [ ]:
import numpy as np

In [ ]:
from lisainstrument import dsp

In [ ]:
from lisainstrument.shift_inversion_numpy import make_shift_inverse_lagrange_numpy

Below is the original shift inversion method from the Instrument class. Only modifications are to make it self-contained, and removed logging.

In [ ]:
def legacy_invert_scet_wrt_tps(
    scet_wrt_tps: np.ndarray,
    clockinv_tolerance: float,
    physics_fs: float,
    interpolation_order: int,
    clockinv_maxiter: int = 5,
):
    edge = min(100, len(scet_wrt_tps) // 2 - 1)
    error = 0

    niter = 0
    next_inverse = scet_wrt_tps
    while not niter or error > clockinv_tolerance:
        if niter >= clockinv_maxiter:
            msg = "Legacy fixed point iter did not converge"
            raise RuntimeError(msg)
        inverse = next_inverse

        next_inverse = dsp.timeshift(
            scet_wrt_tps, -inverse * physics_fs, interpolation_order
        )
    
        error = np.max(np.abs((inverse - next_inverse)[edge:-edge]))
        niter += 1

    return inverse

Setting up some example data

In [ ]:
order = 31
nsamp = 3000
fsample = 16.0
dt = 1 / fsample

f_mod = 0.007
a_mod = 1e-2 / (2 * np.pi * f_mod)
max_it = 5
tol = 1e-10

In [ ]:

def dx_from_x(x):
    return np.cos(2 * np.pi * f_mod * x) * a_mod

xi = np.arange(nsamp) * dt
dxi = dx_from_x(xi)


Set up new shift inversion operator (unchunked pure numpy version)

In [ ]:
op_np = make_shift_inverse_lagrange_numpy(
        order=order,
        fsample=fsample,
        max_abs_shift=a_mod * 1.01,
        max_iter=max_it,
        tolerance=tol,
    )



Compute shift inversion with both

In [ ]:
ai_np = op_np(dxi)
ai_leg = legacy_invert_scet_wrt_tps(dxi, tol/100, fsample, order, max_it+2)

Expected result

In [ ]:
ai_ex = dx_from_x(xi - ai_np)

The original version seems to have more boundary artifacts

In [ ]:
plt.close()
plt.plot(xi, ai_np, "k+")
plt.plot(xi, ai_leg, "rx")
plt.plot(xi, ai_ex, "g-")


The error within the valid points is within the tolerance for both.

In [ ]:
plt.close()
plt.semilogy(xi, np.abs(ai_np-ai_ex), "k+")
plt.semilogy(xi, np.abs(ai_leg-ai_ex), "rx")
plt.axhline(y=tol)
plt.axvline(x=xi[op_np.margin_left])
plt.axvline(x=xi[-op_np.margin_right])


To investigate the differences inside the valid region, fix a bug in the legacy method. It used to return the second-best guess instead of the latest iteration result. Also, we make the margin size for the error measure a parameter.

In [ ]:
def modified_invert_scet_wrt_tps(
    scet_wrt_tps: np.ndarray,
    clockinv_tolerance: float,
    physics_fs: float,
    edge : int,
    interpolation_order: int,
    clockinv_maxiter: int = 15,
):
    
    error = 0

    niter = 0
    next_inverse = scet_wrt_tps
    while not niter or error > clockinv_tolerance:
        if niter >= clockinv_maxiter:
            msg = "Legacy fixed point iter did not converge"
            raise RuntimeError(msg)
        inverse = next_inverse

        next_inverse = dsp.timeshift(
            scet_wrt_tps, -inverse * physics_fs, interpolation_order
        )
    
        error = np.max(np.abs((inverse - next_inverse)[edge:-edge]))
        niter += 1
    print( niter )
    return next_inverse

In [ ]:
#ai_mod = modified_invert_scet_wrt_tps(dxi, tol, fsample, op_np.margin_left, order)
ai_mod = modified_invert_scet_wrt_tps(dxi, tol, fsample, 100, order)

Now the error inside the valid region agrees perfectly (the margin size was not the issue).

In [ ]:
plt.close()
plt.semilogy(xi, np.abs(ai_np-ai_ex), "k+")
plt.semilogy(xi, np.abs(ai_mod-ai_ex), "rx")
plt.axhline(y=tol)
plt.axvline(x=xi[op_np.margin_left])
plt.axvline(x=xi[-op_np.margin_right])


The boundary artifacts are still larger for the legacy algorithm. Reason yet unkown.

In [ ]:
plt.close()
plt.plot(xi, ai_np, "k+")
plt.plot(xi, ai_mod, "rx")
plt.plot(xi, ai_ex, "g-")
plt.xlim(xi[-20], xi[-1]+dt)
